In [9]:
import requests
from datetime import datetime
import pandas as pd
import os
import concurrent.futures
import logging
import time
import gc
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry

# Setup logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Constants
GITHUB_API_URL = "https://api.github.com"
REPO = "audacity/audacity"
#TOKEN = os.getenv("GITHUB_TOKEN")  # Use environment variable
TOKEN = "github_token"

if not TOKEN:
    raise ValueError("GitHub token not found. Set the GITHUB_TOKEN environment variable.")

# Headers for authentication
headers = {
    "Authorization": f"token {TOKEN}"
}

# Introduce a small delay between requests
REQUEST_DELAY = 20  # 30 second


# Helper function to create a retryable session
def get_retry_session(retries=5, backoff_factor=1, status_forcelist=(500, 502, 504), timeout=30):
    session = requests.Session()
    retry = Retry(
        total=retries,
        read=retries,
        connect=retries,
        backoff_factor=backoff_factor,  # Increased to 1 for more wait between retries
        status_forcelist=status_forcelist,
    )
    adapter = HTTPAdapter(max_retries=retry)
    session.mount("http://", adapter)
    session.mount("https://", adapter)
    return session


# Use session for requests with retries and backoff
session = get_retry_session()

def get_pull_request_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching pull request details for PR {pr_number}: {e}")
        return None


def check_rate_limit(headers):
    url = f"{GITHUB_API_URL}/rate_limit"
    try:
        response = session.get(url, headers=headers)
        if response is None:
            logging.error("No response received from GitHub API.")
            return None, None
        response.raise_for_status()
        data = response.json()
        remaining = data['rate']['remaining']
        reset = data['rate']['reset']
        return remaining, reset
    except requests.exceptions.RequestException as e:
        logging.error(f"Error checking rate limit: {e}")
        return None, None


def wait_for_rate_limit_reset(headers):
    remaining, reset = check_rate_limit(headers)
    if remaining == 0:
        reset_time = datetime.fromtimestamp(reset)
        sleep_time = (reset_time - datetime.now()).total_seconds() + 15  # Adding a buffer
        logging.warning(f"Rate limit reached. Sleeping for {sleep_time} seconds.")
        time.sleep(sleep_time)
    else:
        time.sleep(REQUEST_DELAY)  # Add a small delay between requests


def get_pull_requests(repo, headers, max_requests=10000):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls"
    params = {
        "state": "closed",
        "per_page": 10,  # Reduced per_page to lower memory consumption
        "sort": "updated",
        "direction": "desc"
    }
    prs = []
    while len(prs) < max_requests:
        wait_for_rate_limit_reset(headers)
        response = session.get(url, headers=headers, params=params)
        response.raise_for_status()
        batch = response.json()
        if not batch:
            break
        prs.extend(batch)
        if 'next' in response.links:
            url = response.links['next']['url']
        else:
            break
        gc.collect()  # Explicitly free memory after each batch
    return [pr for pr in prs if pr['merged_at']][:max_requests]

# Helper methods to fetch details from GitHub API for a specific pull request (PR)

def get_issue_comments(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/issues/{pr_number}/comments"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching issue comments for PR {pr_number}: {e}")
        return []

def get_review_comments(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}/comments"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching review comments for PR {pr_number}: {e}")
        return []

def get_reviews(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}/reviews"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching reviews for PR {pr_number}: {e}")
        return []

def get_issue_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/issues/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching issue details for PR {pr_number}: {e}")
        return None

def get_pull_request_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching pull request details for PR {pr_number}: {e}")
        return None

# Function to get workflow runs (build runs) associated with a pull request
def get_build_runs(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/actions/runs"
    try:
        # Query workflow runs related to the pull request
        params = {
            'event': 'pull_request',
            'branch': f'pull/{pr_number}/merge'  # GitHub creates temporary refs for PRs
        }
        response = requests.get(url, headers=headers, params=params)
        response.raise_for_status()
        data = response.json()

        # Return the total number of workflow runs associated with this PR
        total_runs = data['total_count']
        logging.info(f"Total build runs for PR {pr_number}: {total_runs}")
        return total_runs
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching build runs for PR {pr_number}: {e}")
        return 0

# Function to get the number of failed workflow runs (build failures) for a pull request
def get_build_failures(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/actions/runs"
    try:
        # Query workflow runs related to the pull request
        params = {
            'event': 'pull_request',
            'branch': f'pull/{pr_number}/merge'  # GitHub creates temporary refs for PRs
        }
        response = requests.get(url, headers=headers, params=params)
        response.raise_for_status()
        data = response.json()

        # Count how many of the workflow runs failed
        failed_runs = sum(1 for run in data['workflow_runs'] if run['conclusion'] == 'failure')
        logging.info(f"Build failures for PR {pr_number}: {failed_runs}")
        return failed_runs
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching build failures for PR {pr_number}: {e}")
        return 0



def extract_metrics(pr, repo, headers, retries=3):
    pr_number = pr['number']
    
    #if pr_number is more than 4000 then skip
    if pr_number > 3000:
        return None
    

    attempt = 0
    while attempt < retries:
        try:
            pr_details = get_pull_request_details(repo, pr_number, headers)
            issue_comments = get_issue_comments(repo, pr_number, headers) or []
            review_comments = get_review_comments(repo, pr_number, headers) or []
            reviews = get_reviews(repo, pr_number, headers) or []
            issue_details = get_issue_details(repo, pr_number, headers)

            # Collect the authors of all comments
            comment_authors = list(set([comment['user']['login'] for comment in issue_comments]))
            
            # Collect the text of all comments
            issue_comments_text = " ".join([comment["body"] for comment in issue_comments])
            review_comments_text = " ".join([comment["body"] for comment in review_comments])
            reviews_text = " ".join([review["body"] for review in reviews if review.get("body")])
            issue_text = issue_details.get("body", "")

            # Assume `num_build_runs` and `num_build_failures` are fetched from a separate function
            num_build_runs = get_build_runs(repo, pr_number, headers)
            num_build_failures = get_build_failures(repo, pr_number, headers)

            metrics = {
                "pr_number": pr_number,
                "created_at": pr_details["created_at"],
                "merged_at": pr_details["merged_at"],
                "author": pr_details["user"]["login"],
                "number_of_comments": len(issue_comments),
                "number_of_review_comments": len(review_comments),
                "number_of_commits": pr_details["commits"],
                "lines_of_code_changed": pr_details["additions"] + pr_details["deletions"],
                "number_of_files_changed": pr_details["changed_files"],
                "number_of_reviewers": len(set([review["user"]["login"] for review in reviews if review["user"]])),
                "number_of_approvals": len([review for review in reviews if review["state"] == "APPROVED"]),
                "labels": [label["name"] for label in pr_details["labels"]],
                "time_to_first_response": (datetime.strptime(issue_comments[0]["created_at"], "%Y-%m-%dT%H:%M:%SZ") - datetime.strptime(pr_details["created_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds() if issue_comments else None,
                "number_of_assignees": len(pr_details["assignees"]),
                "review_duration": (datetime.strptime(pr_details["updated_at"], "%Y-%m-%dT%H:%M:%SZ") - datetime.strptime(pr_details["created_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds(),
                "number_of_changes_requested": len([review for review in reviews if review["state"] == "CHANGES_REQUESTED"]),
                "number_of_build_runs": num_build_runs,
                "number_of_build_failures": num_build_failures,
                "number_of_linked_issues": len(pr_details.get("linked_issues", [])),
                "time_since_last_commit": (datetime.now() - datetime.strptime(pr_details["updated_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds(),
                "test_coverage": pr_details.get("test_coverage"),  # Assuming test coverage is included in PR details
                "number_of_reviews_requested": len(pr_details["requested_reviewers"]),
                "number_of_revisions": pr_details["commits"],
                "number_of_milestones": 1 if pr_details["milestone"] else 0,
                "dependency_changes": any('dependency' in label["name"].lower() for label in pr_details["labels"]),
                "comment_authors": comment_authors,
                "issue_comments_text": issue_comments_text,
                "review_comments_text": review_comments_text,
                "reviews_text": reviews_text,
                "issue_text": issue_text
            }

            return metrics
        except (requests.ConnectionError, requests.Timeout) as e:
            attempt += 1
            logging.warning(f"Connection issue on PR {pr_number}, attempt {attempt}/{retries}. Retrying...")
            time.sleep(10)  # Wait before retrying
        except Exception as e:
            logging.error(f"PR {pr_number} generated an exception: {e}")
            return None


def main():
    prs = get_pull_requests(REPO, headers, max_requests=2000)  # Try fetching 1000 PRs instead of 48000
    if not prs:
        print("No pull requests found.")
        return

    logging.info(f"Fetched {len(prs)} pull requests.")

    metrics_list = []
    with concurrent.futures.ThreadPoolExecutor(max_workers=3) as executor:  # Reduced the number of workers to 1
        future_to_pr = {executor.submit(extract_metrics, pr, REPO, headers): pr for pr in prs}
        for future in concurrent.futures.as_completed(future_to_pr):
            pr = future_to_pr[future]
            try:
                metrics = future.result()
                if metrics:
                    metrics_list.append(metrics)
            except Exception as exc:
                logging.error(f'PR {pr["number"]} generated an exception: {exc}')

    df = pd.DataFrame(metrics_list)
    print(df.head())  # Print the DataFrame to ensure data is correctly captured
    df.to_csv("pull_request_metrics_audacity.csv", index=False)
    print("Data has been saved to pull_request_metrics_audacity.csv")


if __name__ == "__main__":
    main()


2024-09-14 13:11:51,604 - WARNING - Retrying (Retry(total=4, connect=5, read=4, redirect=None, status=None)) after connection broken by 'RemoteDisconnected('Remote end closed connection without response')': /repositories/32921736/pulls?state=closed&per_page=10&sort=updated&direction=desc&page=43&state=closed&per_page=10&sort=updated&direction=desc
2024-09-14 13:15:18,919 - WARNING - Retrying (Retry(total=4, connect=5, read=4, redirect=None, status=None)) after connection broken by 'RemoteDisconnected('Remote end closed connection without response')': /repositories/32921736/pulls?state=closed&per_page=10&sort=updated&direction=desc&page=46&state=closed&per_page=10&sort=updated&direction=desc
2024-09-14 13:18:21,404 - WARNING - Retrying (Retry(total=4, connect=5, read=4, redirect=None, status=None)) after connection broken by 'RemoteDisconnected('Remote end closed connection without response')': /repositories/32921736/pulls?state=closed&per_page=10&sort=updated&direction=desc&page=49&sta

KeyboardInterrupt: 

In [3]:
import requests
from datetime import datetime
import pandas as pd
import os
import concurrent.futures
import logging
import time
import gc
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry

# Setup logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Constants
GITHUB_API_URL = "https://api.github.com"
REPO = "microsoft/PowerToys"
#TOKEN = os.getenv("GITHUB_TOKEN")  # Use environment variable
TOKEN = "github_token"

if not TOKEN:
    raise ValueError("GitHub token not found. Set the GITHUB_TOKEN environment variable.")

# Headers for authentication
headers = {
    "Authorization": f"token {TOKEN}"
}

# Introduce a small delay between requests
REQUEST_DELAY = 20  # 1 second


# Helper function to create a retryable session
def get_retry_session(retries=5, backoff_factor=1, status_forcelist=(500, 502, 504), timeout=30):
    session = requests.Session()
    retry = Retry(
        total=retries,
        read=retries,
        connect=retries,
        backoff_factor=backoff_factor,  # Increased to 1 for more wait between retries
        status_forcelist=status_forcelist,
    )
    adapter = HTTPAdapter(max_retries=retry)
    session.mount("http://", adapter)
    session.mount("https://", adapter)
    return session


# Use session for requests with retries and backoff
session = get_retry_session()

def get_pull_request_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching pull request details for PR {pr_number}: {e}")
        return None


def check_rate_limit(headers):
    url = f"{GITHUB_API_URL}/rate_limit"
    try:
        response = session.get(url, headers=headers)
        if response is None:
            logging.error("No response received from GitHub API.")
            return None, None
        response.raise_for_status()
        data = response.json()
        remaining = data['rate']['remaining']
        reset = data['rate']['reset']
        return remaining, reset
    except requests.exceptions.RequestException as e:
        logging.error(f"Error checking rate limit: {e}")
        return None, None


def wait_for_rate_limit_reset(headers):
    remaining, reset = check_rate_limit(headers)
    if remaining == 0:
        reset_time = datetime.fromtimestamp(reset)
        sleep_time = (reset_time - datetime.now()).total_seconds() + 15  # Adding a buffer
        logging.warning(f"Rate limit reached. Sleeping for {sleep_time} seconds.")
        time.sleep(sleep_time)
    else:
        time.sleep(REQUEST_DELAY)  # Add a small delay between requests


def get_pull_requests(repo, headers, max_requests=10000):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls"
    params = {
        "state": "closed",
        "per_page": 10,  # Reduced per_page to lower memory consumption
        "sort": "updated",
        "direction": "desc"
    }
    prs = []
    while len(prs) < max_requests:
        wait_for_rate_limit_reset(headers)
        response = session.get(url, headers=headers, params=params)
        response.raise_for_status()
        batch = response.json()
        if not batch:
            break
        prs.extend(batch)
        if 'next' in response.links:
            url = response.links['next']['url']
        else:
            break
        gc.collect()  # Explicitly free memory after each batch
    return [pr for pr in prs if pr['merged_at']][:max_requests]

# Helper methods to fetch details from GitHub API for a specific pull request (PR)

def get_issue_comments(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/issues/{pr_number}/comments"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching issue comments for PR {pr_number}: {e}")
        return []

def get_review_comments(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}/comments"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching review comments for PR {pr_number}: {e}")
        return []

def get_reviews(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}/reviews"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching reviews for PR {pr_number}: {e}")
        return []

def get_issue_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/issues/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching issue details for PR {pr_number}: {e}")
        return None

def get_pull_request_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching pull request details for PR {pr_number}: {e}")
        return None

# Function to get workflow runs (build runs) associated with a pull request
def get_build_runs(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/actions/runs"
    try:
        # Query workflow runs related to the pull request
        params = {
            'event': 'pull_request',
            'branch': f'pull/{pr_number}/merge'  # GitHub creates temporary refs for PRs
        }
        response = requests.get(url, headers=headers, params=params)
        response.raise_for_status()
        data = response.json()

        # Return the total number of workflow runs associated with this PR
        total_runs = data['total_count']
        logging.info(f"Total build runs for PR {pr_number}: {total_runs}")
        return total_runs
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching build runs for PR {pr_number}: {e}")
        return 0

# Function to get the number of failed workflow runs (build failures) for a pull request
def get_build_failures(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/actions/runs"
    try:
        # Query workflow runs related to the pull request
        params = {
            'event': 'pull_request',
            'branch': f'pull/{pr_number}/merge'  # GitHub creates temporary refs for PRs
        }
        response = requests.get(url, headers=headers, params=params)
        response.raise_for_status()
        data = response.json()

        # Count how many of the workflow runs failed
        failed_runs = sum(1 for run in data['workflow_runs'] if run['conclusion'] == 'failure')
        logging.info(f"Build failures for PR {pr_number}: {failed_runs}")
        return failed_runs
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching build failures for PR {pr_number}: {e}")
        return 0



def extract_metrics(pr, repo, headers, retries=5):
    pr_number = pr['number']
    attempt = 0
    while attempt < retries:
        try:
            pr_details = get_pull_request_details(repo, pr_number, headers)
            issue_comments = get_issue_comments(repo, pr_number, headers) or []
            review_comments = get_review_comments(repo, pr_number, headers) or []
            reviews = get_reviews(repo, pr_number, headers) or []
            issue_details = get_issue_details(repo, pr_number, headers)

            # Collect the authors of all comments
            comment_authors = list(set([comment['user']['login'] for comment in issue_comments]))
            
            # Collect the text of all comments
            issue_comments_text = " ".join([comment["body"] for comment in issue_comments])
            review_comments_text = " ".join([comment["body"] for comment in review_comments])
            reviews_text = " ".join([review["body"] for review in reviews if review.get("body")])
            issue_text = issue_details.get("body", "")

            # Assume `num_build_runs` and `num_build_failures` are fetched from a separate function
            num_build_runs = get_build_runs(repo, pr_number, headers)
            num_build_failures = get_build_failures(repo, pr_number, headers)

            metrics = {
                "pr_number": pr_number,
                "created_at": pr_details["created_at"],
                "merged_at": pr_details["merged_at"],
                "author": pr_details["user"]["login"],
                "number_of_comments": len(issue_comments),
                "number_of_review_comments": len(review_comments),
                "number_of_commits": pr_details["commits"],
                "lines_of_code_changed": pr_details["additions"] + pr_details["deletions"],
                "number_of_files_changed": pr_details["changed_files"],
                "number_of_reviewers": len(set([review["user"]["login"] for review in reviews if review["user"]])),
                "number_of_approvals": len([review for review in reviews if review["state"] == "APPROVED"]),
                "labels": [label["name"] for label in pr_details["labels"]],
                "time_to_first_response": (datetime.strptime(issue_comments[0]["created_at"], "%Y-%m-%dT%H:%M:%SZ") - datetime.strptime(pr_details["created_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds() if issue_comments else None,
                "number_of_assignees": len(pr_details["assignees"]),
                "review_duration": (datetime.strptime(pr_details["updated_at"], "%Y-%m-%dT%H:%M:%SZ") - datetime.strptime(pr_details["created_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds(),
                "number_of_changes_requested": len([review for review in reviews if review["state"] == "CHANGES_REQUESTED"]),
                "number_of_build_runs": num_build_runs,
                "number_of_build_failures": num_build_failures,
                "number_of_linked_issues": len(pr_details.get("linked_issues", [])),
                "time_since_last_commit": (datetime.now() - datetime.strptime(pr_details["updated_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds(),
                "test_coverage": pr_details.get("test_coverage"),  # Assuming test coverage is included in PR details
                "number_of_reviews_requested": len(pr_details["requested_reviewers"]),
                "number_of_revisions": pr_details["commits"],
                "number_of_milestones": 1 if pr_details["milestone"] else 0,
                "dependency_changes": any('dependency' in label["name"].lower() for label in pr_details["labels"]),
                "comment_authors": comment_authors,
                "issue_comments_text": issue_comments_text,
                "review_comments_text": review_comments_text,
                "reviews_text": reviews_text,
                "issue_text": issue_text
            }

            return metrics
        except (requests.ConnectionError, requests.Timeout) as e:
            attempt += 10
            logging.warning(f"Connection issue on PR {pr_number}, attempt {attempt}/{retries}. Retrying...")
            time.sleep(5)  # Wait before retrying
        except Exception as e:
            logging.error(f"PR {pr_number} generated an exception: {e}")
            return None


def main():
    prs = get_pull_requests(REPO, headers, max_requests=4000)  # Try fetching 1000 PRs instead of 48000
    if not prs:
        print("No pull requests found.")
        return

    logging.info(f"Fetched {len(prs)} pull requests.")

    metrics_list = []
    with concurrent.futures.ThreadPoolExecutor(max_workers=10) as executor:  # Reduced the number of workers to 1
        future_to_pr = {executor.submit(extract_metrics, pr, REPO, headers): pr for pr in prs}
        for future in concurrent.futures.as_completed(future_to_pr):
            pr = future_to_pr[future]
            try:
                metrics = future.result()
                if metrics:
                    metrics_list.append(metrics)
            except Exception as exc:
                logging.error(f'PR {pr["number"]} generated an exception: {exc}')

    df = pd.DataFrame(metrics_list)
    print(df.head())  # Print the DataFrame to ensure data is correctly captured
    df.to_csv("pull_request_metrics_powertoys.csv", index=False)
    print("Data has been saved to pull_request_metrics_powertoys.csv")


if __name__ == "__main__":
    main()


2024-09-11 22:26:18,682 - WARNING - Rate limit reached. Sleeping for 842.317764 seconds.
2024-09-12 00:58:54,687 - INFO - Fetched 3602 pull requests.
2024-09-12 00:58:57,051 - INFO - Total build runs for PR 34819: 0
2024-09-12 00:58:57,055 - INFO - Total build runs for PR 34553: 0
2024-09-12 00:58:57,209 - INFO - Total build runs for PR 34223: 0
2024-09-12 00:58:57,224 - INFO - Total build runs for PR 33494: 0
2024-09-12 00:58:57,319 - INFO - Total build runs for PR 34316: 0
2024-09-12 00:58:57,319 - INFO - Total build runs for PR 34314: 0
2024-09-12 00:58:57,320 - INFO - Total build runs for PR 33457: 0
2024-09-12 00:58:57,320 - INFO - Total build runs for PR 34753: 0
2024-09-12 00:58:57,394 - INFO - Total build runs for PR 34198: 0
2024-09-12 00:58:57,511 - INFO - Build failures for PR 34819: 0
2024-09-12 00:58:57,522 - INFO - Build failures for PR 34553: 0
2024-09-12 00:58:57,527 - INFO - Total build runs for PR 34622: 0
2024-09-12 00:58:57,626 - INFO - Build failures for PR 34223: 

   pr_number            created_at             merged_at          author  \
0      34819  2024-09-11T19:30:57Z  2024-09-11T23:02:10Z     plante-msft   
1      34553  2024-09-03T11:55:10Z  2024-09-05T18:26:46Z         donlaci   
2      34223  2024-08-08T17:12:41Z  2024-08-08T17:52:57Z  jaimecbernardo   
3      34316  2024-08-15T23:00:00Z  2024-08-20T12:24:38Z            dend   
4      34314  2024-08-15T20:37:06Z  2024-08-16T09:16:43Z        snickler   

   number_of_comments  number_of_review_comments  number_of_commits  \
0                   1                          4                  6   
1                   3                          0                  3   
2                   0                          0                  1   
3                   4                          0                  5   
4                   2                          0                  1   

   lines_of_code_changed  number_of_files_changed  number_of_reviewers  ...  \
0                     11             

In [5]:
import requests
from datetime import datetime
import pandas as pd
import os
import concurrent.futures
import logging
import time
import gc
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry

# Setup logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Constants
GITHUB_API_URL = "https://api.github.com"
REPO = "JabRef/jabref"
#TOKEN = os.getenv("GITHUB_TOKEN")  # Use environment variable
TOKEN = "github_token"

if not TOKEN:
    raise ValueError("GitHub token not found. Set the GITHUB_TOKEN environment variable.")

# Headers for authentication
headers = {
    "Authorization": f"token {TOKEN}"
}

# Introduce a small delay between requests
REQUEST_DELAY = 20  # 1 second


# Helper function to create a retryable session
def get_retry_session(retries=5, backoff_factor=1, status_forcelist=(500, 502, 504), timeout=30):
    session = requests.Session()
    retry = Retry(
        total=retries,
        read=retries,
        connect=retries,
        backoff_factor=backoff_factor,  # Increased to 1 for more wait between retries
        status_forcelist=status_forcelist,
    )
    adapter = HTTPAdapter(max_retries=retry)
    session.mount("http://", adapter)
    session.mount("https://", adapter)
    return session


# Use session for requests with retries and backoff
session = get_retry_session()

def get_pull_request_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching pull request details for PR {pr_number}: {e}")
        return None


def check_rate_limit(headers):
    url = f"{GITHUB_API_URL}/rate_limit"
    try:
        response = session.get(url, headers=headers)
        if response is None:
            logging.error("No response received from GitHub API.")
            return None, None
        response.raise_for_status()
        data = response.json()
        remaining = data['rate']['remaining']
        reset = data['rate']['reset']
        return remaining, reset
    except requests.exceptions.RequestException as e:
        logging.error(f"Error checking rate limit: {e}")
        return None, None


def wait_for_rate_limit_reset(headers):
    remaining, reset = check_rate_limit(headers)
    if remaining == 0:
        reset_time = datetime.fromtimestamp(reset)
        sleep_time = (reset_time - datetime.now()).total_seconds() + 15  # Adding a buffer
        logging.warning(f"Rate limit reached. Sleeping for {sleep_time} seconds.")
        time.sleep(sleep_time)
    else:
        time.sleep(REQUEST_DELAY)  # Add a small delay between requests


def get_pull_requests(repo, headers, max_requests=10000):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls"
    params = {
        "state": "closed",
        "per_page": 10,  # Reduced per_page to lower memory consumption
        "sort": "updated",
        "direction": "desc"
    }
    prs = []
    while len(prs) < max_requests:
        wait_for_rate_limit_reset(headers)
        response = session.get(url, headers=headers, params=params)
        response.raise_for_status()
        batch = response.json()
        if not batch:
            break
        prs.extend(batch)
        if 'next' in response.links:
            url = response.links['next']['url']
        else:
            break
        gc.collect()  # Explicitly free memory after each batch
    return [pr for pr in prs if pr['merged_at']][:max_requests]

# Helper methods to fetch details from GitHub API for a specific pull request (PR)

def get_issue_comments(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/issues/{pr_number}/comments"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching issue comments for PR {pr_number}: {e}")
        return []

def get_review_comments(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}/comments"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching review comments for PR {pr_number}: {e}")
        return []

def get_reviews(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}/reviews"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching reviews for PR {pr_number}: {e}")
        return []

def get_issue_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/issues/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching issue details for PR {pr_number}: {e}")
        return None

def get_pull_request_details(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/pulls/{pr_number}"
    try:
        response = session.get(url, headers=headers)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching pull request details for PR {pr_number}: {e}")
        return None

# Function to get workflow runs (build runs) associated with a pull request
def get_build_runs(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/actions/runs"
    try:
        # Query workflow runs related to the pull request
        params = {
            'event': 'pull_request',
            'branch': f'pull/{pr_number}/merge'  # GitHub creates temporary refs for PRs
        }
        response = requests.get(url, headers=headers, params=params)
        response.raise_for_status()
        data = response.json()

        # Return the total number of workflow runs associated with this PR
        total_runs = data['total_count']
        logging.info(f"Total build runs for PR {pr_number}: {total_runs}")
        return total_runs
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching build runs for PR {pr_number}: {e}")
        return 0

# Function to get the number of failed workflow runs (build failures) for a pull request
def get_build_failures(repo, pr_number, headers):
    url = f"{GITHUB_API_URL}/repos/{repo}/actions/runs"
    try:
        # Query workflow runs related to the pull request
        params = {
            'event': 'pull_request',
            'branch': f'pull/{pr_number}/merge'  # GitHub creates temporary refs for PRs
        }
        response = requests.get(url, headers=headers, params=params)
        response.raise_for_status()
        data = response.json()

        # Count how many of the workflow runs failed
        failed_runs = sum(1 for run in data['workflow_runs'] if run['conclusion'] == 'failure')
        logging.info(f"Build failures for PR {pr_number}: {failed_runs}")
        return failed_runs
    except requests.exceptions.RequestException as e:
        logging.error(f"Error fetching build failures for PR {pr_number}: {e}")
        return 0



def extract_metrics(pr, repo, headers, retries=5):
    pr_number = pr['number']
    attempt = 0
    while attempt < retries:
        try:
            pr_details = get_pull_request_details(repo, pr_number, headers)
            issue_comments = get_issue_comments(repo, pr_number, headers) or []
            review_comments = get_review_comments(repo, pr_number, headers) or []
            reviews = get_reviews(repo, pr_number, headers) or []
            issue_details = get_issue_details(repo, pr_number, headers)

            # Collect the authors of all comments
            comment_authors = list(set([comment['user']['login'] for comment in issue_comments]))
            
            # Collect the text of all comments
            issue_comments_text = " ".join([comment["body"] for comment in issue_comments])
            review_comments_text = " ".join([comment["body"] for comment in review_comments])
            reviews_text = " ".join([review["body"] for review in reviews if review.get("body")])
            issue_text = issue_details.get("body", "")

            # Assume `num_build_runs` and `num_build_failures` are fetched from a separate function
            num_build_runs = get_build_runs(repo, pr_number, headers)
            num_build_failures = get_build_failures(repo, pr_number, headers)

            metrics = {
                "pr_number": pr_number,
                "created_at": pr_details["created_at"],
                "merged_at": pr_details["merged_at"],
                "author": pr_details["user"]["login"],
                "number_of_comments": len(issue_comments),
                "number_of_review_comments": len(review_comments),
                "number_of_commits": pr_details["commits"],
                "lines_of_code_changed": pr_details["additions"] + pr_details["deletions"],
                "number_of_files_changed": pr_details["changed_files"],
                "number_of_reviewers": len(set([review["user"]["login"] for review in reviews if review["user"]])),
                "number_of_approvals": len([review for review in reviews if review["state"] == "APPROVED"]),
                "labels": [label["name"] for label in pr_details["labels"]],
                "time_to_first_response": (datetime.strptime(issue_comments[0]["created_at"], "%Y-%m-%dT%H:%M:%SZ") - datetime.strptime(pr_details["created_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds() if issue_comments else None,
                "number_of_assignees": len(pr_details["assignees"]),
                "review_duration": (datetime.strptime(pr_details["updated_at"], "%Y-%m-%dT%H:%M:%SZ") - datetime.strptime(pr_details["created_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds(),
                "number_of_changes_requested": len([review for review in reviews if review["state"] == "CHANGES_REQUESTED"]),
                "number_of_build_runs": num_build_runs,
                "number_of_build_failures": num_build_failures,
                "number_of_linked_issues": len(pr_details.get("linked_issues", [])),
                "time_since_last_commit": (datetime.now() - datetime.strptime(pr_details["updated_at"], "%Y-%m-%dT%H:%M:%SZ")).total_seconds(),
                "test_coverage": pr_details.get("test_coverage"),  # Assuming test coverage is included in PR details
                "number_of_reviews_requested": len(pr_details["requested_reviewers"]),
                "number_of_revisions": pr_details["commits"],
                "number_of_milestones": 1 if pr_details["milestone"] else 0,
                "dependency_changes": any('dependency' in label["name"].lower() for label in pr_details["labels"]),
                "comment_authors": comment_authors,
                "issue_comments_text": issue_comments_text,
                "review_comments_text": review_comments_text,
                "reviews_text": reviews_text,
                "issue_text": issue_text
            }

            return metrics
        except (requests.ConnectionError, requests.Timeout) as e:
            attempt += 10
            logging.warning(f"Connection issue on PR {pr_number}, attempt {attempt}/{retries}. Retrying...")
            time.sleep(5)  # Wait before retrying
        except Exception as e:
            logging.error(f"PR {pr_number} generated an exception: {e}")
            return None


def main():
    prs = get_pull_requests(REPO, headers, max_requests=4000)  # Try fetching 1000 PRs instead of 48000
    if not prs:
        print("No pull requests found.")
        return

    logging.info(f"Fetched {len(prs)} pull requests.")

    metrics_list = []
    with concurrent.futures.ThreadPoolExecutor(max_workers=10) as executor:  # Reduced the number of workers to 1
        future_to_pr = {executor.submit(extract_metrics, pr, REPO, headers): pr for pr in prs}
        for future in concurrent.futures.as_completed(future_to_pr):
            pr = future_to_pr[future]
            try:
                metrics = future.result()
                if metrics:
                    metrics_list.append(metrics)
            except Exception as exc:
                logging.error(f'PR {pr["number"]} generated an exception: {exc}')

    df = pd.DataFrame(metrics_list)
    print(df.head())  # Print the DataFrame to ensure data is correctly captured
    df.to_csv("pull_request_metrics_jabref.csv", index=False)
    print("Data has been saved to pull_request_metrics_jabref.csv")


if __name__ == "__main__":
    main()


2024-09-12 08:07:31,135 - INFO - Fetched 3404 pull requests.
2024-09-12 08:07:33,007 - INFO - Total build runs for PR 11750: 0
2024-09-12 08:07:33,344 - INFO - Build failures for PR 11750: 0
2024-09-12 08:07:33,591 - INFO - Total build runs for PR 11745: 0
2024-09-12 08:07:33,641 - INFO - Total build runs for PR 11709: 0
2024-09-12 08:07:33,665 - INFO - Total build runs for PR 11744: 0
2024-09-12 08:07:33,670 - INFO - Total build runs for PR 11739: 0
2024-09-12 08:07:33,675 - INFO - Total build runs for PR 11747: 0
2024-09-12 08:07:33,681 - INFO - Total build runs for PR 11751: 0
2024-09-12 08:07:33,800 - INFO - Total build runs for PR 11713: 0
2024-09-12 08:07:33,813 - INFO - Total build runs for PR 11746: 0
2024-09-12 08:07:33,927 - INFO - Build failures for PR 11745: 0
2024-09-12 08:07:33,993 - INFO - Build failures for PR 11709: 0
2024-09-12 08:07:34,071 - INFO - Build failures for PR 11751: 0
2024-09-12 08:07:34,073 - INFO - Build failures for PR 11739: 0
2024-09-12 08:07:34,087 -

   pr_number            created_at             merged_at           author  \
0      11750  2024-09-11T02:47:56Z  2024-09-11T05:39:02Z        leaf-soba   
1      11745  2024-09-09T18:13:55Z  2024-09-09T18:40:06Z       Siedlerchr   
2      11709  2024-09-06T02:27:41Z  2024-09-06T07:53:57Z        leaf-soba   
3      11751  2024-09-11T08:55:03Z  2024-09-11T09:22:07Z           koppor   
4      11739  2024-09-09T14:45:35Z  2024-09-10T04:58:21Z  dependabot[bot]   

   number_of_comments  number_of_review_comments  number_of_commits  \
0                   1                          0                  1   
1                   1                          0                  4   
2                   0                          0                  1   
3                   1                          0                  1   
4                   1                          0                  2   

   lines_of_code_changed  number_of_files_changed  number_of_reviewers  ...  \
0                    107       